### 0. Models Used
1.   https://huggingface.co/deepseek-ai/DeepSeek-R1-Distill-Qwen-1.5B
2.   https://huggingface.co/hexgrad/Kokoro-82M

### 1. Preprocessing¶

In [ ]:
!pip install transformers accelerate bitsandbytes
!pip install PyPDF2 pdfplumber requests beautifulsoup4
!pip install -q kokoro>=0.9.2 soundfile
!apt-get -qq -y install espeak-ng > /dev/null 2>&1
!pip install pydub

import torch
from kokoro import KPipeline
from IPython.display import display, Audio
import soundfile as sf
from transformers import pipeline
import requests
import PyPDF2
import pdfplumber
from bs4 import BeautifulSoup
import os
import re
import numpy as np
import soundfile as sf
from IPython.display import Audio
import json
from tqdm.notebook import tqdm

print("GPU Available:", torch.cuda.is_available())
print("GPU Name:", torch.cuda.get_device_name(0) if torch.cuda.is_available() else "None")

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.0/76.0 MB 8.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 31.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 36.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 37.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 10.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 89.4 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstalling

### 2. Functions

In [ ]:
# Function to extract text from PDF
def extract_text_from_pdf(file_path):
    try:
        with pdfplumber.open(file_path) as pdf:
            text = ""
            for page in pdf.pages:
                text += page.extract_text()
            return text
    except Exception as e:
        print(f"Error reading PDF: {e}")
        return None

# Function to fetch the article text from a URL
def fetch_article_text(url):
    try:
        response = requests.get(url, timeout=8)
        response.raise_for_status()
        soup = BeautifulSoup(response.text, 'html.parser')

        article_text = ' '.join([p.get_text() for p in soup.find_all('p') if len(p.get_text().split()) > 30])

        return article_text if article_text else "Content unavailable"
    except requests.RequestException as e:
        print(f"Error fetching {url}: {e}")
        return "Content unavailable"

# Function to extract text from plain text input
def extract_text_from_input(text):
    if text:
        return text
    else:
        print("Error: No text provided.")
        return None

# Function to automatically determine input type and process accordingly
def process_input(input_data):
    # Check if the input is a file and if it's a PDF
    if isinstance(input_data, str) and os.path.isfile(input_data):
        if input_data.lower().endswith(".pdf"):  # If it's a PDF
            text = extract_text_from_pdf(input_data)
        else:
            print("Error: Unsupported file type.")
            return
    # Check if the input is a URL (starts with "http" or "www")
    elif isinstance(input_data, str) and (input_data.startswith("http") or input_data.startswith("www")):
        text = fetch_article_text(input_data)[:500]
    # Check if the input is a string (plain text)
    elif isinstance(input_data, str):
        text = extract_text_from_input(input_data)
    else:
        print("Error: Unsupported input format.")
        return
    return text

def text_model(content, length):
  messages = [
      {
          "role": "user",
          "content": f"""
          You are a podcast scriptwriter. Your task is to create a script for a podcast episode.
          The script should be **engaging**, **informal**, and **conversational**. Write in a way that feels
          like a natural conversation with the audience, using **personal pronouns** (e.g., 'you', 'we', 'us').
          The script should be **dynamic** and **appropriate for a {length} long podcast episode**.
          Use the following example of what I want the output to look like. Give me the script in the
          following format: {example}
          """
      }
  ]

  messages.append(
      {
          "role": "user",
          "content": f"""
          The topic for this podcast is {content}
          """
      }
  )
  pipe = pipeline("text-generation", model="deepseek-ai/DeepSeek-R1-Distill-Qwen-1.5B")
  response = pipe(messages, max_new_tokens=2000)
  return response

def clean_podcast_script(text):
    opening_segment_match = re.search(r'</think>', text)
    if opening_segment_match:
        text = text[opening_segment_match.end():]
    return text.strip()

def tts_model(speaker_1_voice, speaker_1_type, speaker_2_voice,speaker_2_type, podcast_json):
    # Initialize the pipeline for both voices
    pipeline_speaker_1 = KPipeline(lang_code=speaker_1_type)
    pipeline_speaker_2 = KPipeline(lang_code=speaker_2_type)

    # Go through each entry in the 'podcast' and process the lines
    audio_files = []
    for entry in podcast_json['podcast']:
        text_input = entry['line']
        speaker = entry['speaker']

        if speaker == 1:
            voice_type = speaker_1_voice
            pipeline = pipeline_speaker_1
        else:
            voice_type = speaker_2_voice
            pipeline = pipeline_speaker_2

        generator = pipeline(text_input, voice=voice_type)

        for i, (gs, ps, audio) in enumerate(generator):
            result = Audio(data=audio, rate=24000, autoplay=i == 0)
            audio_files.append(result)

    return audio_files

def combined_audio(audio_files):
  combined_audio = []

  for audio in audio_files:
      combined_audio.append(np.frombuffer(audio.data, dtype=np.int16))

  combined_audio = np.concatenate(combined_audio)

  output_filename = 'combined_audio.wav'

  sf.write(output_filename, combined_audio, 24000)

  result = Audio(combined_audio, rate=24000)
  output = display(result)
  return output

example = """
{
    "topic": "AGI",
    "podcast": [
        {
            "speaker": 2,
            "line": "So, AGI, huh? Seems like everyone's talking about it these days."
        },
        {
            "speaker": 1,
            "line": "Yeah, it's definitely having a moment, isn't it?"
        },
        {
            "speaker": 2,
            "line": "It is and for good reason, right? I mean, you've been digging into this stuff, listening to the podcasts and everything. What really stood out to you? What got you hooked?"
        },
        {
            "speaker": 1,
            "line": "Honestly, it's the sheer scale of what AGI could do. We're talking about potentially reshaping well everything."
        },
        {
            "speaker": 2,
            "line": "It certainly is and on that note, we'll wrap up this deep dive. Thanks for listening, everyone."
        },
        {
            "speaker": 1,
            "line": "Peace."
        }
    ]
}
"""

def podcast_model(text, voice_1, voice_1_type, voice_2, voice_2_type, podcast_length):
    steps = [
        "Processing input text",
        "Generating podcast script",
        "Extracting AI response",
        "Cleaning script into JSON",
        "Generating voice audio",
        "Combining final audio"
    ]

    progress = tqdm(steps, desc="Processing", unit="step")

    content = process_input(text)
    progress.update(1)

    deepseek_output = (text_model(content, podcast_length))
    ai_output = deepseek_output[0]
    progress.update(1)

    ai_response = next(item['content'] for item in ai_output['generated_text'] if item['role'] == 'assistant')
    progress.update(1)

    cleaned_output = json.loads(clean_podcast_script(ai_response))
    progress.update(1)

    podcast_audio = tts_model(voice_1, voice_1_type, voice_2, voice_2_type, cleaned_output)
    progress.update(1)

    final_podcast = combined_audio(podcast_audio)
    progress.update(1)

    progress.set_description("Podcast generation complete✅")
    progress.close()

    return final_podcast

### 3. Script Generation

In [ ]:
text_link = "https://www.pbs.org/newshour/politics/how-the-white-house-calculated-trumps-sweeping-new-tariffs"
podcast_model(text_link, 'af_heart', 'a', 'bm_george', 'b', "1 minute")

Processing:   0%|          | 0/6 [00:00<?, ?step/s]

Device set to use cuda:0


config.json:   0%|          | 0.00/2.35k [00:00<?, ?B/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/rnn.py:123: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.2 and num_layers=1
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)


kokoro-v1_0.pth:   0%|          | 0.00/327M [00:00<?, ?B/s]

Processing:  17%|█▋        | 1/6 [05:48<29:01, 348.37s/step]


bm_george.pt:   0%|          | 0.00/523k [00:00<?, ?B/s]

af_heart.pt:   0%|          | 0.00/523k [00:00<?, ?B/s]

### 4. Conclusion

1.   Output on the above conditions/parameters takes ~1 minute from start to finish.
2.   The result is a .wav audio file that can be downloaded.

